# Finding Winners in the Public Markets using Historical Financials

Investors usually look into the past to forecast future results. While this might seem reasonable at first, weighing too heavily on past results eliminates opportunities to make outsized returns in the markets. 

"You can't predict the future through a rearview mirror" - Peter Lynch

What I have found to be extremely useful is combining a quantitative approach on historical data with deep fundamental research. This analysis/model acts as an effective screener but requires an extra step of building domain knowledge and digging into company strategy, management, and industry to solidify one's conviction. 

Using historical financial statement data, I give companies a weighted average score out 10 based on Value, Quality, Growth, Margin Improvement, and Balance Sheet. The scores show me which companies have been doing well (high score) and which companies are struggling (low score). 

Many companies with low scores are left for dead and may be trading at below their intrinsic value, which is why it is important to add an extra step of deep fundamental research and valuation. Conversely, companies with high scores may be trading above and beyond their intrinsic value and investors should tread carefully. 

This file will aggregate and manipulate financial statements form the Simfin API into metrics and measurements that I will need for my analysis. After pickling my final dataset for data persistence, I will construct the scores in the next file, "fulltest3".

***
I downloaded raw data of historical company financials from an api, [Simfin](https://simfin.com/data/bulk). 

There are several other vendors for historical company data, [IEX Cloud](https://iexcloud.io/docs/api/), [Tiingo](https://api.tiingo.com/), [Quandl](https://docs.quandl.com/), or [Polygon.io](https://polygon.io/stocks). I found Simfin most efficient for my use.

***
Note: The data is too broad. In order to increase the accuracy of estimating winners in the market, I need more company-specific(business model categorization, key developments, etc.), industry-specific(for Saas companies I would need lifetime values, average age of a customer, cohort data, etc.), management (tenure, past experience, employee approval) data and more, which becomes expensive to obtain. It is better to focus on a specific sector, obtain very high quality dataset of a handful of companies, and combine the analysis with deep fundamental research and due diligence, rather than trying a top-down approach of analyzing the market as a whole. There is a company doing this for Saas/Technology companies called [PublicComps.com](https://publiccomps.com/). Data is quite expensive at $99/month, but it would be interesting to see analyze their dataset to find winners. 


## Imports and Config

In [1]:
%matplotlib inline
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns

# Import the main functionality from the SimFin Python API.
import simfin as sf

# Import names used for easy access to SimFin's data-columns.
from simfin.names import *

#import datetime
from datetime import datetime, timedelta
from pandas.tseries.offsets import BDay

#display
pd.options.display.max_rows = 5000
pd.options.display.max_columns = 5000

In [2]:
sf.__version__

'0.4.0'

In [3]:
sf.set_data_dir('~/simfin_data/')

In [4]:
# sf.set_api_key(api_key='free')
sf.load_api_key(path='~/simfin_api_key.txt', default_key='free')

## Load Financial Statements

In [5]:
%%time 
#Data for US
market = 'us'

#Load Annual Statements
ttm_is = sf.load_income(variant = 'ttm', market = market, refresh_days = 1)
ttm_bs = sf.load_balance(variant = 'ttm', market = market, refresh_days = 1)
ttm_cf = sf.load_cashflow(variant = 'ttm', market = market, refresh_days = 1)

#Load Quarterly Statements
q_is = sf.load_income(variant = 'quarterly', market = market, refresh_days = 1)
q_bs = sf.load_balance(variant = 'quarterly', market = market, refresh_days = 1)
q_cf = sf.load_cashflow(variant = 'quarterly', market = market, refresh_days = 1)

# Daily Share-Prices.
df_prices = sf.load_shareprices(variant='daily', market=market, refresh_days = 1)

#load companies and industries and merge
df_companies = sf.load_companies(index=TICKER, market='us', refresh_days = 1)
df_industries = sf.load_industries(refresh_days = 1)
df_co_ind = pd.merge(df_companies, df_industries.reset_index(),\
                     how = 'left', left_on = 'IndustryId', right_on = 'IndustryId')

Dataset "us-income-ttm" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-balance-ttm" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-cashflow-ttm" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-income-quarterly" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-balance-quarterly" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-cashflow-quarterly" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-shareprices-daily" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-companies" on disk (0 days old).
- Loading from disk ... Done!
Dataset "industries" on disk (0 days old).
- Loading from disk ... Done!
Wall time: 23.8 s


#### Create Columns

Columns: SimFinID, year, quarter, publish_date, revenue, cost of revenue, gross profit, operating income, net income, diluted shares, research and development (R&D), earning before interest taxes depreciation amorization (EBITDA), EBITDA margin, asset turnover, gross profit margin, net profit margin, cash, short term debt, long term debt, inventory, plant property and equipment, receivables, payables, current_assets, current liabilities, cash from operations, capital expenditures, long term investments, acquisitions or divestitures, cash from investing, dividends paid, share repurchases (buyback), free cash flow, cash from operations margin, free cash flow margin.

In [6]:
# Calculate annualized growth-rates.
income = ttm_is[['SimFinId','Fiscal Year','Fiscal Period', 'Publish Date',\
         REVENUE, COST_REVENUE, GROSS_PROFIT, OPERATING_INCOME, NET_INCOME,SHARES_DILUTED,RD]]\
         .rename(columns = {'SimFinId':'id','Fiscal Year':'year','Fiscal Period':'quarter','Publish Date':'publish_date',\
                            REVENUE: 'revenue', COST_REVENUE: 'cogs', GROSS_PROFIT: 'gp', OPERATING_INCOME:'oi',\
                            NET_INCOME:'ni', SHARES_DILUTED:'shares', RD: 'rnd'})   

#EBITDA
ebitda_oi = pd.DataFrame(sf.ebitda(df_income=ttm_is,
                       df_cashflow=ttm_cf,
                       formula=OP_INCOME)).rename(columns = {'EBITDA':'ebitda_oi'})

ebitda_ni = pd.DataFrame(sf.ebitda(df_income=ttm_is,
                       df_cashflow=ttm_cf,
                       formula=NET_INCOME)).rename(columns = {'EBITDA':'ebitda_ni'})

income_ebitda = pd.concat([income, ebitda_oi, ebitda_ni], axis = 1)
income_ebitda['ebitda'] = (income_ebitda.ebitda_oi + income_ebitda.ebitda_ni)/2
income_ebitda['ebitda_margin'] = income_ebitda['ebitda']/income_ebitda['revenue']

#create Ratios
ratio = sf.fin_signals(df_income_ttm=ttm_is, df_balance_ttm=ttm_bs)
dff = ratio[['Asset Turnover','Gross Profit Margin','Net Profit Margin']]\
      .rename(columns = {'Asset Turnover': 'fat','Gross Profit Margin': 'gp_margin','Net Profit Margin':'np_margin'})

#Balance Sheet and Cash Flow Statement
bs_cf = pd.concat([ttm_bs[[CASH_EQUIV_ST_INVEST, ST_DEBT, LT_DEBT,\
                           INVENTORIES, PPE_NET, ACC_NOTES_RECV, PAYABLES_ACCRUALS,\
                          TOTAL_CUR_ASSETS, TOTAL_CUR_LIAB]],\
                   ttm_cf[[NET_CASH_OPS, CAPEX, NET_CHG_LT_INVEST, NET_CASH_ACQ_DIVEST, NET_CASH_INV, \
                           DIVIDENDS_PAID, CASH_REPURCHASE_EQUITY]]],axis = 1)\
                   .rename(columns = {CASH_EQUIV_ST_INVEST: 'cash', ST_DEBT: 'st_debt', LT_DEBT: 'lt_debt',\
                                      INVENTORIES: 'inventory', PPE_NET: 'ppe', ACC_NOTES_RECV: 'receivables',\
                                      PAYABLES_ACCRUALS: 'payables', TOTAL_CUR_ASSETS: 'current_assets',\
                                      TOTAL_CUR_LIAB: 'current_liabilities', NET_CASH_OPS: 'cfo', CAPEX: 'capex',\
                                      NET_CHG_LT_INVEST: 'lt_invest', NET_CASH_ACQ_DIVEST: 'acq_divest',NET_CASH_INV: 'cfi',\
                                      DIVIDENDS_PAID: 'dividends_paid', CASH_REPURCHASE_EQUITY: 'buyback'})


statements = pd.concat([income_ebitda, dff, bs_cf], axis = 1)
statements.capex.fillna(0, inplace = True)
statements.cfo.fillna(0, inplace = True)
statements['fcf'] = statements.capex + statements.cfo
statements['cfo_margin'] = statements.cfo/statements.revenue
statements['fcf_margin'] = statements.fcf/statements.revenue

I use last twelve months aggregate data for each quarter to smooth out the data.

### Add prices

In [7]:
#reset index
one = statements.reset_index()

#This moves the date down 3 spots. 1/2 is now 1/5. price -> earnings call -> price
two = df_prices[['Close','Adj. Close']].groupby('Ticker').shift(-10).reset_index()

#add a day to publish date to get prices (adding a lag)
statement_price = pd.merge(one, two, how = 'left', left_on = ['Ticker','publish_date'], right_on = ['Ticker','Date'])

### Add Price Change

In [8]:
#price change % dataframe
price_pct = statement_price[['Ticker','Close','Adj. Close']].groupby('Ticker').\
pct_change().shift(-1).rename(columns = {"Close": "close_pct", "Adj. Close":"adj_close_pct"})

#concat price change and df_income statement, ratio, prices
statement_price_pct = pd.concat([statement_price, price_pct], axis =1)

### Add Industries

In [9]:
final = pd.merge(statement_price_pct, df_co_ind, how= 'left', left_on = 'id',right_on = 'SimFinId')

In [10]:
final.sample(10)

Ticker Report Date      id  year quarter publish_date       revenue  \
6246    AVAV  2019-04-30   75856  2019      Q4   2019-06-26  3.142740e+08   
33643    LNN  2019-11-30   80469  2020      Q1   2020-01-09  4.415140e+08   
61274   XPER  2020-03-31  983817  2020      Q1   2020-05-06  3.411650e+08   
32256   KURA  2018-03-31  795981  2018      Q1   2018-05-08           NaN   
4764     APD  2019-09-30  185217  2019      Q4   2019-11-26  8.918900e+09   
55280   TRUP  2015-12-31  640535  2015      Q4   2016-02-17  1.469630e+08   
3480    AMCX  2012-03-31  445716  2012      Q1   2012-05-10  1.241077e+09   
32333   LAKE  2018-04-30  243284  2018      Q1   2018-06-08  9.737000e+07   
13452   CMRO  2012-01-31  692525  2011      Q4   2012-03-16  8.069000e+06   
40518   NVDA  2013-04-30  172199  2013      Q1   2013-05-22  4.310021e+09   

               cogs            gp            oi          ni       shares  \
6246  -1.858710e+08  1.284030e+08  3.382600e+07    47438000   24071713.0   
33643 -3.214800e+08  1.200340e+08  1.635100e+07     9305000   10815500.0   
61274 -7.837000e+06  3.333280e+08 -8.244000e+06   -18111000   49489500.0   
32256           NaN           NaN -4.341500e+07   -42505000   26328250.0   
4764  -5.975500e+09  2.943400e+09  2.144400e+09  1760000000  221600000.0   
55280 -1.329490e+08  1.401400e+07 -1.677500e+07   -17205000   27638443.0   
3480  -4.404800e+08  8.005970e+08  3.526670e+08   139817000   71473250.0   
32333 -6.022100e+07  3.714900e+07  8.420000e+06      596000    7900502.0   
13452 -8.261000e+06 -1.920000e+05 -5.263000e+06    -5310000    7365000.0   
40518 -2.028474e+09  2.281547e+09  6.581940e+08   579990000  623836000.0   

                rnd     ebitda_oi     ebitda_ni        ebitda  ebitda_margin  \
6246  -3.423400e+07  4.149500e+07  5.507600e+07  4.828550e+07       0.153641   
33643 -1.387000e+07  3.169300e+07  2.940800e+07  3.055050e+07       0.069195   
61274 -1.144450e+08 -1.462000e+06  1.596000e+06  6.700000e+04       0.000196   
32256 -3.247900e+07 -4.338800e+07 -4.260800e+07 -4.299800e+07            NaN   
4764  -7.290000e+07  3.227200e+09  3.459900e+09  3.343550e+09       0.374884   
55280           NaN -1.423300e+07 -1.422400e+07 -1.422850e+07      -0.096817   
3480            NaN  4.526400e+08  4.314670e+08  4.420535e+08       0.356185   
32333           NaN  9.196000e+06  9.222000e+06  9.209000e+06       0.094577   
13452 -1.931000e+06 -4.876000e+06 -4.923000e+06 -4.899500e+06      -0.607200   
40518 -1.190541e+09  8.896820e+08  8.888550e+08  8.892685e+08       0.206326   

            fat  gp_margin  np_margin          cash      st_debt  \
6246   0.663840   0.408570   0.150945  3.231950e+08          NaN   
33643  0.878602   0.271869   0.021075  1.209100e+08     210000.0   
61274  0.299567   0.977029  -0.053086  1.420820e+08          NaN   
32256       NaN        NaN        NaN  1.382000e+08    2294000.0   
4764   0.465052   0.330018   0.197334  2.414700e+09   98600000.0   
55280  1.494955   0.095357  -0.117070  4.324400e+07          NaN   
3480        NaN   0.645082   0.112658  2.241820e+08  171820000.0   
32333       NaN   0.381524   0.006121  1.659000e+07     335000.0   
13452       NaN  -0.023795  -0.658074  9.080000e+05          NaN   
40518  0.755062   0.529359   0.134568  3.713351e+09          NaN   

            lt_debt    inventory           ppe   receivables      payables  \
6246            NaN   54056000.0  1.690500e+07  3.105100e+07  1.597200e+07   
33643  1.158050e+08   97284000.0  7.030500e+07  7.931700e+07  3.009700e+07   
61274  3.352930e+08          NaN  3.183600e+07  3.083500e+07  4.109100e+07   
32256  4.861000e+06          NaN  5.000000e+03           NaN  9.057000e+06   
4764   3.227400e+09  388300000.0  1.033760e+10  1.260200e+09  1.722300e+09   
55280  0.000000e+00          NaN  9.719000e+06  8.196000e+06  5.478000e+06   
3480   2.250105e+09          NaN  6.242900e+07  2.853780e+08  1.160980e+08   
32333  1.273000e+06   44411000.0  8.821000e+06  1.457800e+07  1.103

### Add more features

Adding market capitalization, cash as a % of marketcap, free cash flow yield, cash from operations yield, shareholder yield, enterprise value (EV), ev/sales, ev/ebitda, PPE as % of EV, current ratio, debt to ebitda.

In [11]:
final['mc'] = final['shares'] * final['Close']
final['cash_mc'] = final['cash']/final['mc']
final['fcf_yield'] = final['fcf']/final['mc']
final['cfo_yield'] = final['cfo']/final['mc']
final['se_yield'] = -(final['dividends_paid'] + final['buyback'])/final['mc']
final['ev'] = final['mc'] + np.where(final['st_debt'].isnull(), 0, final['st_debt']) + \
              np.where(final['lt_debt'].isnull(), 0, final['lt_debt']) - final['cash']
final['ev_sales'] = final['ev']/final['revenue']
final['ev_ebitda'] = final['ev']/final['ebitda']

In [12]:
#balance sheet features
final['bs_ppe_apev'] = (np.where(final['ppe'].isnull(),0,final['ppe']) + np.where(final['cash'].isnull(),0,final['cash'])
                        - np.where(final['lt_debt'].isnull(),0,final['lt_debt']))/final['ev']
final['bs_current_ratio'] = final['current_assets']/final['current_liabilities']


#backwards scale
final['bs_debt_ebitda'] = np.where(final['lt_debt'].isnull(),0,\
                                   np.where(final['ebitda']<0, np.nan, final['lt_debt'])/final['ebitda'])



In [13]:
def percent_change(a,x,new_names):
    a = a.reset_index('Ticker',drop = True)
    return pd.DataFrame(np.where(a<0, -(a - a.shift(x))/a, (a - a.shift(x))/a)).rename(columns = new_names)

### Added growth variables

revenue growth, gross profit growth, operating income growth, net income growth, ebitda growth, cash from ops growth, fcf growth, ebitda growth, fixed asset turnover growth, gross profit margin growth, net income margin growth, cash from ops. margin growth, fcf margin growth. 

by quarter, one year, and two year.

In [14]:
growth_var = final[['Ticker','Report Date','revenue','gp','oi','ni','ebitda','cfo','fcf',\
    'ebitda_margin','fat','gp_margin','np_margin','cfo_margin','fcf_margin']].set_index(['Ticker','Report Date'])

#QUARTERLY
# rename_dict_q = {0: 'rev_growth_q', 1:'gp_growth_q',2: 'oi_growth_q',3:'ni_growth_q', 4: 'ebitda_growth_q',5:'cfo_growth_q',\
#               6:'fcf_growth_q',7:'ebitda_margrow_q',8:'fat_growth_q',9:'gp_margrow_q', 10: 'np_margrow_q',
#               11: 'cfo_margrow_q', 12: 'fcf_margrow_q'}

# growth_q = growth_var.groupby('Ticker').apply(percent_change,1,rename_dict_q)

#1 YEAR CHANGE
rename_dict_1 = {0: 'rev_growth_1', 1:'gp_growth_1',2: 'oi_growth_1',3:'ni_growth_1', 4: 'ebitda_growth_1',5:'cfo_growth_1',\
              6:'fcf_growth_1',7:'ebitda_margrow_1',8:'fat_growth_1',9:'gp_margrow_1', 10: 'np_margrow_1',
              11: 'cfo_margrow_1', 12: 'fcf_margrow_1'}

growth_1 = growth_var.groupby('Ticker').apply(percent_change,4,rename_dict_1)

# 2 YEAR CHANGE 
# rename_dict_2 = {0: 'rev_growth_2', 1:'gp_growth_2',2: 'oi_growth_2',3:'ni_growth_2', 4: 'ebitda_growth_2',5:'cfo_growth_2',\
#               6:'fcf_growth_2',7:'ebitda_margrow_2',8:'fat_growth_2',9:'gp_margrow_2', 10: 'np_margrow_2',
#               11: 'cfo_margrow_2', 12: 'fcf_margrow_2'}

# growth_2 = growth_var.groupby('Ticker').apply(percent_change,8,rename_dict_2)


# growth = pd.concat([growth_q, growth_1, growth_2], axis =1).reset_index(drop = True)

df = pd.concat([final, growth_1.reset_index(drop = True)], axis = 1)

df['lt_invest_apr'] = -df['lt_invest']/df['revenue']
df['acq_divest_apr'] = -df['acq_divest']/df['revenue']
df['cf_invest_apr'] = -df['cfi']/df['revenue']

### Pull the latest data for each company into a dataset

In [15]:
latest_price = sf.load_shareprices(variant='latest', market='us', refresh_days = 1)
latest_price = latest_price.reset_index()[['Ticker','Close','Volume']].rename(columns = {'Close':'latest_close'})

Dataset "us-shareprices-latest" on disk (6 days old).
- Downloading ... 100.0%
- Extracting zip-file ... Done!
- Loading from disk ... Done!


In [16]:
test = df.loc[(df.groupby('Ticker')['Report Date'].idxmax())].loc[(df.year >= 2019)&(~df.Close.isnull())]

In [17]:
latest = pd.merge(test, latest_price, how = 'left', left_on = 'Ticker', right_on = 'Ticker')

In [18]:
#add more features
latest['mc'] = latest.shares * latest.latest_close
latest['cash_mc'] = latest.cash/latest.mc
latest['fcf_yield'] = latest['fcf']/latest['mc']
latest['cfo_yield'] = latest['cfo']/latest['mc']
latest['se_yield'] = -(latest.dividends_paid + latest.buyback)/df['mc']
latest['ev'] = latest.mc + np.where(latest.st_debt.isnull(), 0, latest.st_debt) + np.where(latest.lt_debt.isnull(), 0, latest.lt_debt) - latest.cash
latest['ev_sales'] = latest.ev/latest.revenue
latest['ev_ebitda'] = latest.ev/latest.ebitda

#balance sheet features
latest['bs_ppe_apev'] = (np.where(latest['ppe'].isnull(),0,latest['ppe']) + np.where(latest['cash'].isnull(),0,latest['cash'])
                        - np.where(latest['lt_debt'].isnull(),0,latest['lt_debt']))/latest['ev']

#add most recent prices
latest['close_pct'] = latest.latest_close/latest.Close -1

In [19]:
# latest_dict = latest[['Ticker','Report Date','close_pct']].groupby(['Ticker','Report Date']).mean().to_dict()

# df.loc[df.groupby('Ticker')['Report Date'].idxmax(), 'close_pct'] = df.loc[df.groupby('Ticker')['Report Date'].idxmax()]\
# .apply(lambda x: latest_dict['close_pct'][(x[0],x[1])], axis =1 )

In [20]:
#Business Services, Consumer Cyclical, Consumer Defensive, Industrials, Technology
# late = latest[latest.Sector.isin([np.nan,'Business Services', 'Consumer Cyclical', 'Consumer Defensive', 'Industrials', 'Technology','Other'])]

# Create Pickle

We have two datasets: one with latest company data and another with a full dataset of all historical company data.

In [21]:
import _pickle as cPickle
df.to_pickle('dfpickle')
latest.to_pickle('latestpickle')

In [22]:
df.sample(5)

Ticker Report Date      id  year quarter publish_date       revenue  \
31776    KMI  2017-03-31   88392  2017      Q1   2017-04-21  1.328700e+10   
35010   MASI  2016-09-30  350340  2016      Q3   2016-11-02  6.786970e+08   
1784     AEO  2011-01-31  173396  2010      Q4   2011-03-11  2.945294e+09   
34151    LSI  2018-06-30  901127  2018      Q2   2018-08-02  5.397480e+08   
61926   ZIOP  2018-03-31  795980  2018      Q1   2018-05-08           NaN   

               cogs            gp            oi         ni        shares  \
31776 -3.759000e+09  9.528000e+09  3.851000e+09  833000000  2.230250e+09   
35010 -2.374820e+08  4.412150e+08  1.276530e+08  109474000  5.293000e+07   
1784  -1.763143e+09  1.182151e+09  3.395520e+08  140647000  2.018180e+08   
34151 -1.235150e+08  4.162330e+08  2.081820e+08  129744000  4.654411e+07   
61926           NaN           NaN -6.066200e+07  -54856000  1.394774e+08   

              rnd     ebitda_oi     ebitda_ni        ebitda  ebitda_margin  \
31776         NaN  6.067000e+09  5.888000e+09  5.977500e+09       0.449876   
35010 -58665000.0  1.440890e+08  1.612860e+08  1.526875e+08       0.224972   
1784          NaN  4.812140e+08  4.039530e+08  4.425835e+08       0.150268   
34151         NaN  3.094680e+08  3.091790e+08  3.093235e+08       0.573089   
61926 -43300000.0 -6.025500e+07 -5.444900e+07 -5.735200e+07            NaN   

            fat  gp_margin  np_margin         cash       st_debt  \
31776  0.157749   0.717092   0.062693  396000000.0  3.928000e+09   
35010  1.274625   0.650091   0.161300  125988000.0           NaN   
1784        NaN   0.401369   0.047753  734695000.0  1.620300e+07   
34151  0.138729   0.771162   0.240379    7327000.0  1.248900e+07   
61926       NaN        NaN        NaN   51108000.0           NaN   

            lt_debt    inventory           ppe   receivables      payables  \
31776  3.428500e+10  380000000.0  3.902300e+10  1.263000e+09  1.922000e+09   
35010  1.525000e+08   67047000.0  1.331500e+08  9.437400e+07  1.121980e+08   
1784            NaN  301208000.0  6.911790e+08  3.672100e+07  3.055350e+08   
34151  1.723062e+09          NaN  3.675667e+09  7.935000e+06  8.325400e+07   
61926           NaN          NaN  1.244000e+06  1.800000e+04  9.484000e+06   

       current_assets  current_liabilities           cfo         capex  \
31776    2.675000e+09         6.689000e+09  4.594000e+09 -2.328000e+09   
35010    3.246220e+08         1.443350e+08  1.495030e+08 -2.825400e+07   
1784     1.126351e+09         3.878370e+08  4.104160e+08 -7.870500e+07   
34151    1.625600e+07         1.058230e+08  2.504320e+08  0.000000e+00   
61926    7.211500e+07         1.006200e+07 -5.934900e+07 -5.290000e+05   

         lt_invest   acq_divest           cfi  dividends_paid      buyback  \
31776          NaN  986000000.0 -1.131000e+09   -1.275000e+09          NaN   
35010          NaN          NaN -2.921700e+07             NaN  -58807000.0   
1784   114675000.0          NaN  3.597000e+07   -1.831660e+08 -208798000.0   
34151          NaN          NaN -6.553800e+07   -1.857360e+08          NaN   
61926          NaN          NaN -5.290000e+05             NaN   46598000.0   

                fcf  cfo_margin  fcf_margin       Date   Close  Adj. Close  \
31776  2.266000e+09    0.345751    0.170543 2017-04-21   20.19       17.35   
35010  1.212490e+08    0.220279    0.178650 2016-11-02   61.66       61.66   
1784   3.317110e+08    0.139346    0.112624 2011-03-11   15.50       11.08   
34151  2.504320e+08    0.463979    0.463979 2018-08-02  100.93       92.83   
61926 -5.987800e+07         NaN         NaN 2018-05-08    4.39        4.39   

       close_pct  adj_close_pct  SimFinId                   Company Name  \
31776  -0.001981       0.004035     88392            KINDER MORGAN, INC.   
35010   0.508433       0.508433    350340                    MASIMO CORP   
1784   -0.181935      -0.181408    173396  AMERICAN EAGLE OUTFITTERS INC   
34151  -0.047459      -0.036842    901127           

In [23]:
latest.sample(5)

Ticker Report Date      id  year quarter publish_date       revenue  \
1459    TTD  2020-06-30  650768  2020      Q2   2020-08-07  6.801620e+08   
1284   SERV  2020-06-30  749230  2020      Q2   2020-08-07  2.025000e+09   
1114   PAYX  2020-05-31  106287  2020      Q4   2020-07-17  4.040500e+09   
66     AKER  2020-06-30  592461  2020      Q2   2020-08-14  8.620240e+05   
579    FIVE  2020-07-31  902627  2020      Q2   2020-09-03  1.691577e+09   

              cogs            gp            oi          ni       shares  \
1459 -1.695400e+08  5.106220e+08  6.957100e+07   119535000   48262250.0   
1284 -1.190000e+09  8.350000e+08  2.260000e+08    67000000  134750000.0   
1114 -1.280800e+09  2.759700e+09  1.460500e+09  1098100000  361000000.0   
66   -1.182525e+06 -3.205010e+05 -8.927215e+06    -9343067    2221977.0   
579  -1.123467e+09  5.681100e+08  1.177320e+08    99562000   55947965.0   

              rnd     ebitda_oi     ebitda_ni        ebitda  ebitda_margin  \
1459 -138840000.0  9.521600e+07  9.411800e+07  9.466700e+07       0.139183   
1284          NaN  3.360000e+08  2.770000e+08  3.065000e+08       0.151358   
1114          NaN  1.670200e+09  1.646800e+09  1.658500e+09       0.410469   
66     -4526706.0 -8.860418e+06 -9.394499e+06 -9.127458e+06     -10.588404   
579           NaN  1.804520e+08  1.804520e+08  1.804520e+08       0.106677   

           fat  gp_margin  np_margin         cash      st_debt       lt_debt  \
1459  0.548761   0.750736   0.175745  555318000.0          NaN  1.420000e+08   
1284  0.421261   0.412346   0.033086  302000000.0  104000000.0  1.620000e+09   
1114  0.465710   0.683010   0.271773  932400000.0    5100000.0  7.968000e+08   
66    0.145321  -0.371801 -10.838523   18303522.0          NaN           NaN   
579   1.019380   0.335846   0.058858  202008000.0          NaN           NaN   

        inventory          ppe  receivables     payables  current_assets  \
1459          NaN   96075000.0  869064000.0  699315000.0    1.491819e+09   
1284   45000000.0  189000000.0  205000000.0  310000000.0    1.504000e+09   
1114          NaN  407400000.0  384100000.0  774000000.0    5.464600e+09   
66            0.0       4783.0       2301.0    2625572.0    1.847792e+07   
579   294057000.0  505299000.0          NaN  366193000.0    5.705260e+08   

      current_liabilities           cfo        capex    lt_invest  \
1459         7.307000e+08  1.884090e+08  -61219000.0  -27735000.0   
1284         6.820000e+08  2.680000e+08  -27000000.0          NaN   
1114         4.426900e+09  1.440900e+09 -136800000.0  914800000.0   
66           2.705590e+06 -5.347032e+06          0.0   -2907640.0   
579          3.661930e+08  2.014470e+08 -212810000.0   37232000.0   

       acq_divest          cfi  dividends_paid      buyback           fcf  \
1459          NaN  -88954000.0             NaN   77727000.0  1.271900e+08   
1284 -400000000.0 -444000000.0             NaN -129000000.0  2.410000e+08   
1114          NaN  771900000.0    -889400000.0 -171900000.0  1.304100e+09   
66            NaN   -2901390.0             NaN          NaN -5.347032e+06   
579           NaN -175578000.0             NaN  -39644000.0 -1.136300e+07   

      cfo_margin  fcf_margin       Date   Close  Adj. Close  close_pct  \
1459    0.277006    0.187000 2020-08-07  461.78      461.78   0.311339   
1284    0.132346    0.119012 2020-08-07   39.72       39.72   0.076536   
1114    0.356614    0.322757 2020-07-17   71.92       71.92   0.141129   
66     -6.202881   -6.202881 2020-08-14    2.72        2.72  -0.150735   
579     0.119088   -0.006717 2020-09-03  136.68      136.68  -0.030875   

      adj_close_pct  SimFinId                       Company Name  IndustryId  \
1459            NaN    650768                   Trade Desk, Inc.    101003.0   
1284            NaN    749230  SERVICEMASTER GLOBAL HOLDINGS INC    100002.0   
1114            NaN    106287                        PAYCHEX INC    100002.0   
66              NaN    592461            Akers 

# 52 week low prices

Screen for companies trading at their 52 week low prices

In [24]:
from datetime import date
from dateutil.relativedelta import relativedelta

today = date.today()
twoyears = today - relativedelta(years =2)
twoyears = pd.to_datetime(twoyears)

price = df_prices.reset_index()
price = price.loc[price.Date > twoyears]

low = price.loc[price.groupby('Ticker')['Close'].idxmin().dropna(),['Ticker','Date','Close','Adj. Close']]
high = price.loc[price.groupby('Ticker')['Close'].idxmax().dropna(),['Ticker','Date','Close','Adj. Close']]

price_today = sf.load_shareprices(variant='latest', market='us', refresh_days = 1).reset_index()
price_today = price_today.loc[price_today.Date == price_today.Date.max(),['Ticker','Date','Close','Adj. Close']]

Dataset "us-shareprices-latest" on disk (0 days old).
- Loading from disk ... Done!


In [25]:
price_df_low = pd.merge(low, price_today, on = 'Ticker', how = 'inner')
price_df_low['Date'] = price_df_low.Date_y - price_df_low.Date_x
price_df_low['close_diff'] = price_df_low.Close_y/price_df_low.Close_x -1
price_df_low['adjclose_diff'] = price_df_low['Adj. Close_y']/price_df_low['Adj. Close_x'] -1
price_df_low

Ticker     Date_x    Close_x  Adj. Close_x     Date_y    Close_y  \
0            A 2018-10-24      61.13         60.09 2020-10-08     104.16   
1           AA 2020-03-20       5.48          5.48 2020-10-08      12.73   
2          AAL 2020-05-15       9.04          9.04 2020-10-08      13.15   
3         AAMC 2019-08-01       7.99          7.99 2020-10-08      20.40   
4         AAME 2019-11-13       1.50          1.50 2020-10-08       2.00   
5          AAN 2020-03-20      15.00         14.98 2020-10-08      59.73   
6         AAOI 2020-03-18       5.50          5.50 2020-10-08      11.59   
7         AAON 2018-10-11      31.84         31.38 2020-10-08      62.77   
8          AAP 2020-03-20      75.03         74.77 2020-10-08     157.66   
9         AAPL 2019-01-03      35.55         34.78 2020-10-08     114.97   
10        AAWW 2020-03-12      16.41         16.42 2020-10-08      67.43   
11        AAXN 2018-12-24      39.74         39.74 2020-10-08      97.07   
12          AB 2020-03-18      14.66         13.96 2020-10-08      29.74   
13        ABBV 2019-08-15      62.98         59.68 2020-10-08      87.34   
14         ABC 2018-12-24      70.76         68.52 2020-10-08      98.49   
15        ABCB 2020-05-13      18.52         18.28 2020-10-08      26.43   
16         ABG 2020-04-03      42.10         42.10 2020-10-08     115.15   
17         ABM 2020-03-23      20.45         20.08 2020-10-08      37.48   
18        ABMC 2019-09-09       0.06          0.06 2020-10-08       0.22   
19        ABMD 2020-03-20     130.51        130.51 2020-10-08     271.20   
20         ABT 2020-03-23      62.82         62.33 2020-10-08     108.54   
21          AC 2020-03-23      26.18         25.96 2020-10-08      34.11   
22         ACA 2018-10-30      21.00         20.80 2020-10-08      46.72   
23        ACAD 2018-12-24      14.32         14.32 2020-10-08      43.18   
24        ACCO 2020-03-23       3.89          3.81 2020-10-08       6.44   
25        ACET 2020-03-18       6.12          6.12 2020-10-08      12.64   
26        ACGL 2020-05-13      22.24         22.24 2020-10-08      31.50   
27        ACHC 2020-03-23      11.78         11.78 2020-10-08      32.12   
28        ACIA 2018-10-29      33.45         33.45 2020-10-08      67.57   
29        ACLS 2020-03-19      13.42         13.42 2020-10-08      23.49   
30        ACLZ 2019-10-16       0.02          0.02 2020-10-08       0.04   
31         ACM 2020-03-18      23.82         23.82 2020-10-08      46.08   
32         ACN 2018-12-24     133.67        130.41 2020-10-08     225.61   
33        ACRX 2020-03-23       0.76          0.76 2020-10-08       1.59   
34         ACT 2020-03-23      16.16         16.16 2020-10-08      27.22   
35         ACY 2020-04-06       0.80          0.80 2020-10-08       1.97   
36        ADBE 2018-12-24     205.16        205.16 2020-10-08     490.84   
37        ADES 2020-09-21       3.76          3.76 2020-10-08       4.74   
38         ADI 2018-10-24      77.82         74.62 2020-10-08     120.34   
39        ADIL 2020-03-23       1.05          1.05 2020-10-08       2.10   
40         ADM 2020-03-23      29.31         28.78 2020-10-08      48.85   
41        ADMA 2020-03-18       1.50          1.50 2020-10-08       2.50   
42         ADP 2020-03-23     109.07        107.64 2020-10-08     147.01   
43        ADPT 2020-03-16      16.96         16.96 2020-10-08      50.78   
44         ADS 2020-03-18      22.61         22.38 2020-10-08      48.41   
45        ADSK 2018-12-24     118.32        118.32 2020-10-08     234.31   
46         ADT 2020-03-23       3.72          3.69 2020-10-08       8.41   
47        ADVM 2018-12-21       2.87          2.87 2020-10-08      11.06   
48          AE 2020-03-18      16.24         15.92 2020-10-08      19.82   
49         AEE 2020-03-23      61.37         60.58 2020-10-08      81.73   
50        AEHR 2019-01-17       1.06          1.06 2020-10-08       1.41   
51        AEIS 2020-03-18      35.55         35.55 2020-

In [26]:
price_df_low.sort_values('adjclose_diff')

Ticker     Date_x    Close_x  Adj. Close_x     Date_y    Close_y  \
1804      YOGA 2020-09-28       0.04          0.05 2020-10-08       0.04   
900       JSDA 2020-10-06       0.15          0.16 2020-10-08       0.15   
1311      PROM 2020-07-15       0.06          0.06 2020-10-08       0.06   
923       KONA 2019-10-07       0.01          0.02 2020-10-08       0.02   
1095      MSGO 2020-04-02       0.01          0.01 2020-10-08       0.01   
645       FLLZ 2018-10-10      14.00         14.00 2020-10-08      14.00   
987       LRDC 2020-06-03       0.01          0.01 2020-10-08       0.01   
1669      UIHC 2020-10-08       5.88          5.88 2020-10-08       5.88   
277        BTU 2020-10-08       2.06          2.06 2020-10-08       2.06   
582       ETEC 2019-11-15       0.10          0.10 2020-10-08       0.10   
1593      TLRD 2020-10-01       0.09          0.09 2020-10-08       0.09   
1319      PSSR 2020-07-15       0.25          0.25 2020-10-08       0.25   
291       CAGU 2020-06-08       0.16          0.16 2020-10-08       0.16   
164       ASNB 2020-05-04       0.02          0.02 2020-10-08       0.02   
822       ICPT 2020-10-08      37.69         37.69 2020-10-08      37.69   
152       AREX 2019-11-26       0.01          0.02 2020-10-08       0.01   
1619      TRNX 2020-10-08       0.02          0.02 2020-10-08       0.02   
1358      REMI 2019-02-19       0.14          0.14 2020-10-08       0.14   
222        BFB 2020-10-08      78.00         78.00 2020-10-08      78.00   
1445       SGA 2020-09-28      19.78         19.78 2020-10-08      19.90   
464        CXW 2020-10-07       7.91          7.91 2020-10-08       7.99   
1406      SAFT 2020-09-23      67.16         67.16 2020-10-08      68.00   
525        DYN 2020-10-07      18.74         18.74 2020-10-08      18.99   
1362       REV 2020-09-24       6.28          6.28 2020-10-08       6.38   
1291       PMD 2020-10-07       4.32          4.32 2020-10-08       4.42   
155       ARLP 2020-10-07       2.76          2.76 2020-10-08       2.83   
163       ASNA 2020-09-11       0.28          0.28 2020-10-08       0.29   
1134      NEOS 2020-10-06       0.50          0.50 2020-10-08       0.52   
1699       UVE 2020-09-29      13.69         13.69 2020-10-08      14.29   
1414      SATS 2020-10-02      24.38         24.38 2020-10-08      25.57   
1812      ZGNX 2020-09-25      17.50         17.50 2020-10-08      18.45   
1727       VRS 2020-10-01       7.76          7.76 2020-10-08       8.19   
107       AMCI 2019-01-29       9.68          9.68 2020-10-08      10.28   
79         AKR 2020-09-23      10.08         10.08 2020-10-08      10.71   
205       BABY 2020-09-24      16.65         16.65 2020-10-08      17.70   
750       HAYN 2020-09-30      17.09         17.09 2020-10-08      18.21   
1744       WBA 2020-09-10      34.67         34.67 2020-10-08      37.07   
568        EPM 2020-03-18       2.16          2.12 2020-10-08       2.27   
906       KANP 2020-03-18      25.00         25.00 2020-10-08      26.82   
1234      PAHC 2020-10-02      17.04         17.04 2020-10-08      18.30   
347        CHK 2020-09-01       3.73          3.74 2020-10-08       4.02   
1309      PRLE 2019-11-26       1.20          1.20 2020-10-08       1.29   
1696       UTL 2020-09-23      37.49         37.49 2020-10-08      40.38   
800       HSTM 2020-09-23      19.64         19.64 2020-10-08      21.18   
210       BBGI 2020-09-22       1.22          1.22 2020-10-08       1.32   
740       GTXI 2020-09-30       1.70          1.70 2020-10-08       1.84   
178        AVA 2020-03-23      33.04         32.34 2020-10-08      35.03   
1421      SCHL 2020-09-24      19.95         19.95 2020-10-08      21.61   
1753       WHG 2020-03-18      11.05         11.05 2020-10-08      11.98   
1182       NWE 2020-09-23      48.01         48.01 2020-10-08      52.10   
770        HII 2020-09-10     137.83        137.83 2020-10-08     149.64   
1656      TYME 2020-03-18       0.90          0.90 2020-

In [27]:
price_df_high = pd.merge(high, price_today, on = 'Ticker', how = 'inner')
price_df_high['Date'] = price_df_high.Date_y - price_df_high.Date_x
price_df_high['close_diff'] = price_df_high.Close_y/price_df_high.Close_x -1
price_df_high['adjclose_diff'] = price_df_high['Adj. Close_y']/price_df_high['Adj. Close_x'] -1
price_df_high.sort_values('adjclose_diff', ascending = True)

Ticker     Date_x    Close_x  Adj. Close_x     Date_y    Close_y  \
1619      TRNX 2018-11-13      43.00         43.00 2020-10-08       0.02   
1095      MSGO 2019-06-06       5.95          5.95 2020-10-08       0.01   
965       LKSD 2018-11-02      10.92          9.89 2020-10-08       0.02   
580        ESV 2018-10-15      35.28         35.13 2020-10-08       0.09   
882       JBCT 2018-12-11      16.80         16.80 2020-10-08       0.05   
1532      STLR 2019-02-01     308.40        308.40 2020-10-08       0.95   
163       ASNA 2018-10-15      92.40         92.40 2020-10-08       0.29   
482       DEST 2018-11-13       5.60          5.60 2020-10-08       0.02   
483         DF 2018-10-30       8.08          8.04 2020-10-08       0.03   
347        CHK 2018-10-16     964.00        964.00 2020-10-08       4.02   
1593      TLRD 2018-12-03      23.77         21.46 2020-10-08       0.09   
1276       PIR 2018-10-30      35.80         35.80 2020-10-08       0.18   
1397      RSLS 2018-10-18     536.23        530.88 2020-10-08       3.50   
923       KONA 2018-10-12       2.29          2.29 2020-10-08       0.02   
152       AREX 2018-10-10       2.11          2.11 2020-10-08       0.01   
1166      NSPR 2018-10-18      13.18         13.18 2020-10-08       0.32   
78        AKER 2018-10-30      90.17         90.24 2020-10-08       2.31   
183       AVGR 2018-10-10      11.50         11.50 2020-10-08       0.31   
1457      SIGN 2019-04-04       2.95          2.95 2020-10-08       0.10   
1803      YGYI 2018-10-15      15.88         15.88 2020-10-08       0.54   
1070       MNK 2018-11-12      31.60         31.60 2020-10-08       1.09   
1804      YOGA 2019-03-20       1.12          1.12 2020-10-08       0.04   
943       LBUY 2019-02-05       1.65          1.65 2020-10-08       0.06   
1594      TLRY 2018-10-15     165.64        165.64 2020-10-08       6.15   
271       BSPM 2018-10-10       1.35          1.35 2020-10-08       0.06   
804        HTZ 2020-02-20      20.29         20.29 2020-10-08       1.12   
1401      RWLK 2018-10-10      21.25         21.25 2020-10-08       1.20   
625        FET 2018-10-16      10.06         10.06 2020-10-08       0.59   
725       GPOR 2018-10-16      11.20         11.20 2020-10-08       0.66   
1478      SMLP 2018-10-23      16.86         13.07 2020-10-08       0.78   
1512      SQBG 2019-03-01      80.40         80.40 2020-10-08       4.96   
277        BTU 2018-10-16      36.39         33.12 2020-10-08       2.06   
1644      TUSK 2018-10-16      29.11         28.57 2020-10-08       1.87   
443        CSU 2018-11-05       9.56          9.56 2020-10-08       0.65   
1377       RIG 2018-10-12      13.19         13.19 2020-10-08       0.90   
668       FRAN 2018-10-10      40.46         40.44 2020-10-08       2.81   
1212       ONS 2019-02-15      10.56         10.56 2020-10-08       0.75   
606       EXPR 2018-11-08       9.57          9.57 2020-10-08       0.73   
802       HTGM 2018-11-07       4.16          4.16 2020-10-08       0.33   
1434      SDPI 2018-10-22       5.04          5.04 2020-10-08       0.41   
459       CVSI 2018-11-05       6.40          6.40 2020-10-08       0.54   
1271       PHX 2018-10-16      18.50         18.00 2020-10-08       1.65   
1424      SCOR 2019-02-25      23.22         23.22 2020-10-08       2.16   
994      LTRPA 2018-11-08      20.07         20.07 2020-10-08       1.87   
522       DXLG 2018-11-05       3.43          3.43 2020-10-08       0.32   
1335       QEP 2018-10-10      11.29         11.05 2020-10-08       1.05   
1357       REI 2018-10-15       8.42          8.42 2020-10-08       0.84   
1540       SUP 2018-10-16      13.38         12.62 2020-10-08       1.26   
334       CETX 2018-10-10      10.96         10.96 2020-10-08       1.10   
987       LRDC 2018-10-12       0.09          0.09 2020-10-08       0.01   
687        GCI 2018-10-17      16.11         13.45 2020-10-08       1.50   
1591      TLCC 2018-11-06       0.89          0.89 2020-

# +15% revenue growth

Screen for companies trading at above 15% revenue growth. 

In [28]:
latest.loc[(latest.ev_sales < 3)&(latest.rev_growth_1 > .15)].sort_values('Industry')

Ticker Report Date       id  year quarter publish_date       revenue  \
119    AOBC  2020-07-31   952565  2021      Q1   2020-09-03  8.326900e+08   
1312    SMG  2020-06-30   355003  2020      Q3   2020-08-05  3.739000e+09   
1319   SMSI  2020-06-30   504067  2020      Q2   2020-08-10  5.031500e+07   
1258   SAIC  2020-07-31    54785  2020      Q2   2020-09-03  6.691000e+09   
644    GLUU  2020-06-30    85988  2020      Q2   2020-08-07  4.605460e+08   
541     EVH  2020-06-30   146041  2020      Q2   2020-08-07  9.425850e+08   
794     IVZ  2020-06-30   378170  2020      Q2   2020-07-31  6.481300e+09   
39     ADRO  2020-06-30   781554  2020      Q2   2020-08-03  2.795600e+07   
1497   UMRX  2020-06-30   808945  2020      Q2   2020-08-11  2.386700e+07   
1371   SURF  2020-06-30   808799  2020      Q2   2020-08-11  3.937500e+07   
1037   NLNK  2020-06-30   809595  2020      Q2   2020-08-14  7.330000e+05   
404    CTMX  2020-06-30   789985  2020      Q2   2020-08-06  8.519200e+07   
900    LXRX  2020-06-30    56235  2020      Q2   2020-07-29  3.203370e+08   
378    CRIS  2020-06-30   168118  2020      Q2   2020-08-04  1.121200e+07   
218    BLCM  2020-06-30   808260  2020      Q2   2020-08-06  5.236000e+06   
164    AVEO  2020-06-30   809080  2020      Q2   2020-08-10  2.801400e+07   
1147    PJT  2020-06-30   158528  2020      Q2   2020-07-31  8.556130e+08   
201    BGCP  2020-06-30   625540  2020      Q2   2020-08-07  2.130548e+09   
959     MMS  2020-06-30   447855  2020      Q3   2020-08-06  3.292667e+09   
1445   TROX  2020-06-30   627774  2020      Q2   2020-07-30  2.761000e+09   
1108    PAH  2020-06-30   687589  2020      Q2   2020-08-04  1.759000e+09   
761    INFN  2020-06-30   346530  2020      Q2   2020-08-06  1.371768e+09   
356    COMM  2020-06-30   446289  2020      Q2   2020-08-06  8.814900e+09   
895    LTRX  2020-06-30   172507  2020      Q4   2020-09-11  5.987800e+07   
1052   NTGR  2020-06-30   591520  2020      Q2   2020-07-31  1.028844e+09   
897    LUNA  2020-06-30   816577  2020      Q2   2020-08-06  7.358593e+07   
715     HPJ  2019-06-30   163221  2019      Q2   2019-08-13  3.131451e+08   
512     ENR  2020-06-30   674540  2020      Q3   2020-08-05  2.700800e+09   
47     AEIS  2020-06-30   574583  2020      Q2   2020-08-05  1.168731e+09   
860     LGL  2020-06-30   528980  2020      Q2   2020-08-12  3.310400e+07   
1262   SANW  2020-03-31   246310  2020      Q3   2020-05-14  1.005627e+08   
1066    NWL  2020-06-30   378194  2020      Q2   2020-08-05  9.883300e+09   
1457   TSSI  2020-06-30   363007  2020      Q2   2020-08-14  4.163100e+07   
510     ENG  2020-06-30    58098  2020      Q2   2020-08-06  6.780400e+07   
581     FIX  2020-06-30  1014353  2020      Q2   2020-07-27  2.870101e+09   
1356    SSP  2020-06-30   688615  2020      Q2   2020-08-07  1.583967e+09   
1266   SBGI  2020-06-30   132115  2020      Q2   2020-08-10  5.639178e+09   
1561    WCG  2019-09-30   745218  2019      Q3   2019-10-30  2.698330e+10   
345     CNC  2020-06-30   378107  2020      Q2   2020-07-28  9.157600e+10   
1468   TVTY  2020-06-30   895523  2020      Q2   2020-08-07  1.176939e+09   
859    LGIH  2020-06-30   530141  2020      Q2   2020-08-04  2.025059e+09   
696      HI  2020-06-30   361523  2020      Q3   2020-08-05  2.309100e+09   
1494   ULBI  2020-06-30   739637  2020      Q2   2020-07-30  1.128900e+08   
1430   TPIC  2020-06-30   180206  2020      Q2   2020-08-06  1.536402e+09   
96     AMDA  2020-06-30   498391  2020      Q2   2020-08-12  8.360000e+05   
1245   RSLS  2020-06-30   794492  2020      Q2   2020-08-13  1.205600e+07   
844    LAKE  2020-07-31   243284  2020      Q2   2020-09-14  1.362560e+08   
292     CDE  2020-03-31   529633  2020      Q1   2020-04-22  7.297990e+08   
488     ECA  2019-09-30   897579  2019      Q3   2019-11-04  7.542000e+09   
633    GEOS  2020-06-30   357500  2020      Q3   2020-08-07  1.032460e+08   
933    MEET  2020-06-30   652598  2020      Q2   2020-08-07  2.555857e+08   
1

In [29]:
latest.loc[(latest.ev_sales > 3)&(latest.rev_growth_1 < .15)].sort_values('Industry')

Ticker Report Date       id  year quarter publish_date       revenue  \
1012   NCMI  2020-06-30   716509  2020      Q2   2020-08-03  3.264000e+08   
256    BWXT  2020-06-30   914354  2020      Q2   2020-08-03  2.053963e+09   
162    AVAV  2020-07-31    75856  2021      Q1   2020-09-10  3.678350e+08   
692     HEI  2020-07-31   250786  2020      Q3   2020-08-27  1.902360e+09   
786      IT  2020-06-30   447532  2020      Q2   2020-08-04  4.196021e+09   
909    MAMS  2019-06-30   265007  2019      Q4   2019-09-30  3.771400e+07   
911    MANH  2020-06-30   105128  2020      Q2   2020-07-27  6.047370e+08   
159    ATVI  2020-06-30      243  2020      Q2   2020-08-04  6.988000e+09   
514     ENV  2020-06-30   978454  2020      Q2   2020-08-10  9.578680e+08   
496    EGAN  2020-06-30   233349  2020      Q4   2020-09-11  7.272900e+07   
802    JCOM  2020-06-30   625587  2020      Q2   2020-08-10  1.413106e+09   
1129   PEGA  2020-06-30   448267  2020      Q2   2020-07-28  9.862110e+08   
572    FFIV  2020-06-30    60283  2020      Q3   2020-08-05  2.326394e+09   
118    ANSS  2020-06-30   126145  2020      Q2   2020-08-05  1.520773e+09   
1125   PDFS  2020-06-30   606334  2020      Q2   2020-08-06  8.704300e+07   
879    LOGM  2020-06-30   641732  2020      Q2   2020-07-29  1.312731e+09   
1381   SYMC  2020-06-30   427444  2020      Q1   2020-08-06  1.857000e+09   
184    AZPN  2020-03-31   445871  2020      Q3   2020-05-06  5.866190e+08   
1110   PANW  2020-07-31   199345  2020      Q4   2020-09-04  3.408400e+09   
1363   STMP  2020-06-30   650092  2020      Q2   2020-08-07  6.551500e+08   
301    CERN  2020-06-30   259186  2020      Q2   2020-07-30  5.613750e+09   
1354   SSNC  2020-06-30   721918  2020      Q2   2020-08-05  4.659400e+09   
1339   SPLK  2020-07-31    51255  2020      Q2   2020-09-03  2.343253e+09   
221    BLKB  2020-06-30   445967  2020      Q2   2020-08-04  9.145710e+08   
574    FICO  2020-06-30   446774  2020      Q3   2020-07-29  1.225550e+09   
233     BOX  2020-07-31    47121  2020      Q2   2020-09-04  7.365950e+08   
294    CDNS  2020-06-30   107614  2020      Q2   2020-07-20  2.435533e+09   
293     CDK  2020-06-30   749032  2020      Q4   2020-08-06  1.960100e+09   
1326   SNPS  2020-07-31   744723  2020      Q3   2020-08-21  3.510923e+09   
1240     RP  2020-06-30   243720  2020      Q2   2020-08-04  1.072249e+09   
254    BVSN  2019-09-30   156413  2019      Q3   2019-11-19  3.948000e+06   
1172   PRGS  2020-05-31   748103  2020      Q2   2020-07-08  4.338200e+08   
107   AMSWA  2020-04-30   196458  2020      Q4   2020-07-10  1.154660e+08   
571    FEYE  2020-06-30   276492  2020      Q2   2020-07-31  9.156220e+08   
65     AKAM  2020-06-30    69211  2020      Q2   2020-08-07  3.041052e+09   
1541   VRNT  2020-04-30    44422  2020      Q1   2020-06-09  1.275670e+09   
1005   NATI  2020-06-30    56422  2020      Q2   2020-08-04  1.318620e+09   
950    MJCO  2020-03-31   110826  2019      Q4   2020-07-08  1.464450e+08   
32     ADBE  2020-08-31    14099  2020      Q3   2020-09-23  1.243594e+10   
397    CSOD  2020-06-30   747052  2020      Q2   2020-08-10  6.290400e+08   
764    INOV  2020-06-30   497806  2020      Q2   2020-07-29  6.563440e+08   
768    INTU  2020-07-31   183557  2020      Q4   2020-08-31  7.679000e+09   
929    MDSO  2019-06-30   497390  2019      Q2   2019-08-06  6.845570e+08   
1053   NTNX  2020-04-30   544815  2020      Q3   2020-06-04  1.279684e+09   
1540   VRNS  2020-06-30   908839  2020      Q2   2020-08-04  2.589500e+08   
1055   NUAN  2020-03-31   448077  2020      Q2   2020-05-08  1.707425e+09   
984    MSFT  2020-06-30    59265  2020      Q4   2020-07-30  1.430150e+11   
1480   TYPE  2019-06-30   344785  2019      Q2   2019-07-26  2.439590e+08   
1478    TYL  2020-06-30   693134  2020      Q2   2020-07-29  1.111869e+09   
481      EA  2020-06-30   372651  2020      Q1   2020-08-07  5.787000e+09   
1088   OMCL  2020-06-30   495083  2020      Q2   2020-07-31  9.064040e+08   
4